In [1]:
using JLD

In [2]:
using Images

GROUND_TRUTH_FOLDER = "/Users/manvithaponnapati/RAISR/train_data/ground_truth/"
LOW_RES_FOLDER = "/Users/manvithaponnapati/RAISR/train_data/low_res/"
INTERPOLATED_FOLDER = "/Users/manvithaponnapati/RAISR/train_data/interpolated/"

"/Users/manvithaponnapati/RAISR/train_data/interpolated/"

In [3]:
scale_factor = 2

2

In [4]:
# Pkg.add("Distributions")
@everywhere function hashkey(patch,weights_matrix,patchsize)
    gx,gy = imgradients(patch,KernelFactors.ando3)
    gx = reshape(gx,patchsize*patchsize,1)
    gy = reshape(gy,patchsize*patchsize,1)
    GT = transpose([gx gy])
   
    GTWG = GT*weights_matrix*transpose(GT)
    
    eigen_max = eigmax(GTWG)
    eigen_min = eigmin(GTWG)
    eigen_vector_max = eigvecs(GTWG)[:,1]
    eigen_vector_min = eigvecs(GTWG)[:,2]
    gradient_angle = atan2(eigen_vector_max[2],eigen_vector_max[1])
    if gradient_angle < 0
        gradient_angle = gradient_angle + pi
    end
    lamda = abs(sqrt(complex(eigen_max)))/Qstrength
    u =(sqrt(complex(eigen_max)) -  sqrt(complex(eigen_min)))/(sqrt(complex(eigen_max)) +  sqrt(complex(eigen_min)))/Qcoherence
    angle = floor(gradient_angle/pi*Qangle)

    if lamda < 0.0001
        strength = 1
    elseif lamda > 0.001
        strength = 3
    else
        strength = 2
    end

    u = abs(u)
    if u < 0.25
        coherence = 1
    elseif u > 0.5
        coherence = 3
    else
        coherence = 2
    end


    # Bound the output to the desired ranges
    if angle > 23
        angle = 23
    elseif angle <= 0
        angle = 1
    end
    angle = Int(angle)
    return angle,strength,coherence
end

In [5]:
using Distributions
#Calculate image properties
#Taking 3x3 patches on the imahes 
Qangle = 24
Qstrength = 3
Qcoherence = 3
patchsize = 5
gradientsize = 9
Q = zeros((Qangle, Qstrength, Qcoherence, scale_factor*scale_factor, patchsize*patchsize, patchsize*patchsize))
V = zeros((Qangle, Qstrength, Qcoherence, scale_factor*scale_factor, patchsize*patchsize))
mark = zeros((Qstrength*Qcoherence, Qangle, scale_factor*scale_factor))

start_index = Int(ceil(patchsize/2))
weights_matrix = rand(Normal(0, 2), 9)
weights_matrix = Array(Diagonal(weights_matrix))
#the really really twosted conversions on JuliaImages
filenames = readdir(INTERPOLATED_FOLDER)
for file in filenames
     if (contains("$file", ".jpg")) == true
        println("File nm: $file")
        low_res_im = load(INTERPOLATED_FOLDER*file)
        ground_truth_im = load(GROUND_TRUTH_FOLDER*file)
        
        colorview_rgb = channelview(YCbCr.(low_res_im))
        color_ve = colorview_rgb[1,:,:]/255
        
        colorview_rgb_gt = channelview(YCbCr.(ground_truth_im))
        color_ve_gt = colorview_rgb_gt[1,:,:]/255
        
        w,h = size(color_ve)
        println("Starting file")
        @time for row in start_index:Int(w)-start_index
            for col in start_index:Int(h)-start_index
                
                patch = color_ve[row-2:row+2,col-2:col+2]
                gradientpatch = color_ve[row-1:row+1,col-1:col+1]
                angle,strength,coherence = hashkey(gradientpatch,weights_matrix,3)
#                 println("$angle,$strength,$coherence")
                # Get pixel type
                pixeltype = ((row-start_index) % scale_factor) * scale_factor + ((col-start_index) % scale_factor)
                pixelHR = color_ve_gt[row,col]
#                 println(pixelHR)
                # Compute A'A and A'b
                
                wp,hp = size(patch)
                patch_1 = reshape(patch,wp*hp,1)
                patch = reshape(patch,wp*hp)
                ATA = dot(transpose(patch_1),patch_1)
                ATb = patch*pixelHR
                
                Q[angle,strength,coherence,pixeltype+1,:,:] += ATA
                V[angle,strength,coherence,pixeltype+1,:] +=ATb
                mark[coherence*3+strength, angle, pixeltype+1] += 1
            end
        end

    end
end



File nm: 100007.jpg
Starting file
 21.080308 seconds (55.57 M allocations: 8.348 GiB, 8.03% gc time)
File nm: 100039.jpg
Starting file
 16.089338 seconds (53.51 M allocations: 8.245 GiB, 8.89% gc time)
File nm: 100075.jpg
Starting file
 16.102962 seconds (53.52 M allocations: 8.245 GiB, 9.00% gc time)
File nm: 100080.jpg
Starting file
 15.668923 seconds (53.38 M allocations: 8.242 GiB, 8.89% gc time)
File nm: 100098.jpg
Starting file
 16.480282 seconds (53.51 M allocations: 8.245 GiB, 9.12% gc time)
File nm: 100099.jpg
Starting file
 19.969927 seconds (53.49 M allocations: 8.245 GiB, 8.20% gc time)
File nm: 10081.jpg
Starting file
 17.720577 seconds (53.43 M allocations: 8.243 GiB, 8.71% gc time)
File nm: 101027.jpg
Starting file
 18.715250 seconds (53.51 M allocations: 8.245 GiB, 9.19% gc time)
File nm: 101084.jpg
Starting file
 25.851378 seconds (53.52 M allocations: 8.245 GiB, 7.74% gc time)
File nm: 102062.jpg
Starting file
 23.266718 seconds (53.52 M allocations: 8.245 GiB, 7.68% 

 17.303521 seconds (53.42 M allocations: 8.243 GiB, 8.72% gc time)
File nm: 147062.jpg
Starting file
 22.102013 seconds (53.50 M allocations: 8.245 GiB, 7.97% gc time)
File nm: 147077.jpg
Starting file
 21.695767 seconds (53.51 M allocations: 8.245 GiB, 8.15% gc time)
File nm: 147080.jpg
Starting file
 20.320927 seconds (53.51 M allocations: 8.245 GiB, 8.37% gc time)
File nm: 15004.jpg
Starting file
 19.182026 seconds (53.52 M allocations: 8.245 GiB, 8.64% gc time)
File nm: 15011.jpg
Starting file
 18.972438 seconds (53.51 M allocations: 8.245 GiB, 8.80% gc time)
File nm: 15062.jpg
Starting file
 18.625745 seconds (53.51 M allocations: 8.245 GiB, 9.54% gc time)
File nm: 15088.jpg
Starting file
 18.134625 seconds (53.48 M allocations: 8.245 GiB, 8.68% gc time)
File nm: 151087.jpg
Starting file
 18.252870 seconds (53.46 M allocations: 8.244 GiB, 8.61% gc time)
File nm: 153077.jpg
Starting file
 18.752484 seconds (53.47 M allocations: 8.244 GiB, 8.87% gc time)
File nm: 153093.jpg
Starting

 14.933532 seconds (53.45 M allocations: 8.244 GiB, 11.45% gc time)
File nm: 20008.jpg
Starting file
 14.929292 seconds (53.47 M allocations: 8.244 GiB, 11.26% gc time)
File nm: 20069.jpg
Starting file
 14.913011 seconds (53.49 M allocations: 8.245 GiB, 11.35% gc time)
File nm: 201080.jpg
Starting file
 14.769596 seconds (53.38 M allocations: 8.242 GiB, 11.27% gc time)
File nm: 2018.jpg
Starting file
 15.038371 seconds (53.49 M allocations: 8.245 GiB, 12.11% gc time)
File nm: 202000.jpg
Starting file
 14.886556 seconds (53.44 M allocations: 8.244 GiB, 11.54% gc time)
File nm: 202012.jpg
Starting file
 15.189217 seconds (53.52 M allocations: 8.245 GiB, 11.66% gc time)
File nm: 206062.jpg
Starting file
 14.934575 seconds (53.48 M allocations: 8.245 GiB, 11.31% gc time)
File nm: 206097.jpg
Starting file
 14.929938 seconds (53.52 M allocations: 8.245 GiB, 11.53% gc time)
File nm: 207038.jpg
Starting file
 14.980231 seconds (53.51 M allocations: 8.245 GiB, 11.47% gc time)
File nm: 207049.jp

 15.097981 seconds (53.52 M allocations: 8.245 GiB, 11.96% gc time)
File nm: 27059.jpg
Starting file
 15.106537 seconds (53.48 M allocations: 8.245 GiB, 11.98% gc time)
File nm: 271008.jpg
Starting file
 15.103826 seconds (53.51 M allocations: 8.245 GiB, 11.99% gc time)
File nm: 271031.jpg
Starting file
 15.175491 seconds (53.43 M allocations: 8.243 GiB, 12.56% gc time)
File nm: 274007.jpg
Starting file
 15.617349 seconds (53.52 M allocations: 8.245 GiB, 11.46% gc time)
File nm: 277053.jpg
Starting file
 20.321766 seconds (53.52 M allocations: 8.245 GiB, 9.52% gc time)
File nm: 277095.jpg
Starting file
 16.354246 seconds (53.50 M allocations: 8.245 GiB, 10.10% gc time)
File nm: 279005.jpg
Starting file
 14.473792 seconds (53.41 M allocations: 8.243 GiB, 10.39% gc time)
File nm: 28075.jpg
Starting file
 14.608980 seconds (53.52 M allocations: 8.245 GiB, 10.17% gc time)
File nm: 28083.jpg
Starting file
 14.730219 seconds (53.51 M allocations: 8.245 GiB, 10.52% gc time)
File nm: 28096.jpg

 21.312789 seconds (53.51 M allocations: 8.245 GiB, 8.10% gc time)
File nm: 393035.jpg
Starting file
 20.138800 seconds (53.37 M allocations: 8.242 GiB, 8.32% gc time)
File nm: 41004.jpg
Starting file
 17.374394 seconds (53.46 M allocations: 8.244 GiB, 9.92% gc time)
File nm: 41006.jpg
Starting file
 23.483637 seconds (53.51 M allocations: 8.245 GiB, 7.61% gc time)
File nm: 41025.jpg
Starting file
 18.114285 seconds (53.49 M allocations: 8.245 GiB, 8.36% gc time)
File nm: 41029.jpg
Starting file
 17.872368 seconds (53.49 M allocations: 8.245 GiB, 8.51% gc time)
File nm: 41085.jpg
Starting file
 16.698004 seconds (53.51 M allocations: 8.245 GiB, 9.32% gc time)
File nm: 41096.jpg
Starting file
 16.471183 seconds (53.48 M allocations: 8.245 GiB, 9.11% gc time)
File nm: 42044.jpg
Starting file
 17.465527 seconds (53.31 M allocations: 8.241 GiB, 9.48% gc time)
File nm: 42078.jpg
Starting file
 14.675343 seconds (53.38 M allocations: 8.242 GiB, 10.84% gc time)
File nm: 43033.jpg
Starting fil

In [8]:
#We can get more "sample" 8 more learning samples from the patches we learnt already - basically free training
P = zeros((patchsize*patchsize, patchsize*patchsize, 7))
rotate = zeros((patchsize*patchsize, patchsize*patchsize))
flip = zeros((patchsize*patchsize, patchsize*patchsize))

for i in range(1, patchsize*patchsize-1)
    i1 = i % patchsize
    i2 = Int(ceil(i / patchsize))
    j = (patchsize * patchsize - patchsize + i2 - patchsize * i1)+1 
    rotate[j,i] = 1
    k = patchsize * (i2 + 1) - i1 - 4
    flip[k,i] = 1
end

for i in range(1, 7)
    i1 = i % 4
    i2 = ceil(i / 4)
    P[:,:,i] = dot((flip^i2),(rotate^i1))
end
Qextended = zeros((Qangle, Qstrength, Qcoherence, scale_factor*scale_factor, patchsize*patchsize, patchsize*patchsize))
Vextended = zeros((Qangle, Qstrength, Qcoherence, scale_factor*scale_factor, patchsize*patchsize))

for pixeltype in range(1, scale_factor*scale_factor)
    for angle in range(1, Qangle)
        for strength in range(1, Qstrength)
            for coherence in range(1, Qcoherence)
                for m in range(1, 7)
                    m1 = m % 4
                    m2 = floor(m / 4)
                    newangleslot = angle
                    if m2 == 1
                        newangleslot = Qangle-angle-1
                    end
                    newangleslot = Int(newangleslot-Qangle/2*m1)
                    while newangleslot < 0
                        newangleslot += Qangle
                    end
                    
                    newQ = transpose(P[:,:,m])*(Q[angle,strength,coherence,pixeltype,:,:])*(P[:,:,m])
                    newV = transpose(P[:,:,m])*(V[angle,strength,coherence,pixeltype,:])
                    Qextended[newangleslot+1,strength,coherence,pixeltype,:,:] += newQ
                    Vextended[newangleslot+1,strength,coherence,pixeltype,:] += newV
                end
            end
        end
    end
end
Q += Qextended
V += Vextended

24×3×3×4×25 Array{Float64,5}:
[:, :, 1, 1, 1] =
   312.768  2.73386e5  1.51023e7
 18052.9    7.84268e5  4.12689e7
 12372.6    4.9492e5   3.2132e7 
 16004.7    4.85328e5  3.00628e7
 32353.6    1.57259e6  2.81815e7
 19007.2    6.35521e5  2.74388e7
 14839.5    5.72632e5  2.655e7  
 34079.8    1.68446e6  2.76738e7
 12479.4    4.48516e5  2.9803e7 
 16829.8    5.29373e5  3.26062e7
 19184.9    6.8774e5   3.77062e7
   331.115  3.12016e5  1.74145e7
   210.441  1.58377e5  9.48346e6
 14992.3    8.18865e5  4.38976e7
 14113.6    4.80908e5  3.16932e7
 15961.3    4.66113e5  2.93068e7
 19272.3    1.04567e6  2.70538e7
 27109.5    6.65189e5  2.69241e7
 25458.5    6.7256e5   2.77961e7
 23789.4    1.36126e6  2.81395e7
 12318.5    4.62336e5  3.05928e7
 18072.1    5.43315e5  3.36295e7
 17070.0    8.15531e5  4.42301e7
   246.919  2.29877e5  1.3293e7 

[:, :, 2, 1, 1] =
 517867.0             6.05856e6  7.33449e7
      1.12738e7       2.05669e6  8.92711e7
  31875.7             1.16895e6  3.30604e7
   2991.77  

In [9]:
using Krylov
h = zeros((Qangle, Qstrength, Qcoherence, scale_factor*scale_factor, patchsize*patchsize))
operationcount = 0
totaloperations = scale_factor * scale_factor * Qangle * Qstrength * Qcoherence
for pixeltype in range(1, scale_factor*scale_factor)
    for angle in range(1, Qangle)
        for strength in range(1, Qstrength)
            for coherence in range(1, Qcoherence)
                println(" K: index $pixeltype,$angle, $strength, $coherence")
                operationcount += 1
                x,stats = cgls(Q[angle,strength,coherence,pixeltype,:,:], V[angle,strength,coherence,pixeltype,:])
                h[angle,strength,coherence,pixeltype,:] = x
            end
        end
    end
end

 K: index 1,1, 1, 1
 K: index 1,1, 1, 2
 K: index 1,1, 1, 3
 K: index 1,1, 2, 1
 K: index 1,1, 2, 2
 K: index 1,1, 2, 3
 K: index 1,1, 3, 1
 K: index 1,1, 3, 2
 K: index 1,1, 3, 3
 K: index 1,2, 1, 1
 K: index 1,2, 1, 2
 K: index 1,2, 1, 3
 K: index 1,2, 2, 1
 K: index 1,2, 2, 2
 K: index 1,2, 2, 3
 K: index 1,2, 3, 1
 K: index 1,2, 3, 2
 K: index 1,2, 3, 3
 K: index 1,3, 1, 1
 K: index 1,3, 1, 2
 K: index 1,3, 1, 3
 K: index 1,3, 2, 1
 K: index 1,3, 2, 2
 K: index 1,3, 2, 3
 K: index 1,3, 3, 1
 K: index 1,3, 3, 2
 K: index 1,3, 3, 3
 K: index 1,4, 1, 1
 K: index 1,4, 1, 2
 K: index 1,4, 1, 3
 K: index 1,4, 2, 1
 K: index 1,4, 2, 2
 K: index 1,4, 2, 3
 K: index 1,4, 3, 1
 K: index 1,4, 3, 2
 K: index 1,4, 3, 3
 K: index 1,5, 1, 1
 K: index 1,5, 1, 2
 K: index 1,5, 1, 3
 K: index 1,5, 2, 1
 K: index 1,5, 2, 2
 K: index 1,5, 2, 3
 K: index 1,5, 3, 1
 K: index 1,5, 3, 2
 K: index 1,5, 3, 3
 K: index 1,6, 1, 1
 K: index 1,6, 1, 2
 K: index 1,6, 1, 3
 K: index 1,6, 2, 1
 K: index 1,6, 2, 2


 K: index 3,8, 2, 2
 K: index 3,8, 2, 3
 K: index 3,8, 3, 1
 K: index 3,8, 3, 2
 K: index 3,8, 3, 3
 K: index 3,9, 1, 1
 K: index 3,9, 1, 2
 K: index 3,9, 1, 3
 K: index 3,9, 2, 1
 K: index 3,9, 2, 2
 K: index 3,9, 2, 3
 K: index 3,9, 3, 1
 K: index 3,9, 3, 2
 K: index 3,9, 3, 3
 K: index 3,10, 1, 1
 K: index 3,10, 1, 2
 K: index 3,10, 1, 3
 K: index 3,10, 2, 1
 K: index 3,10, 2, 2
 K: index 3,10, 2, 3
 K: index 3,10, 3, 1
 K: index 3,10, 3, 2
 K: index 3,10, 3, 3
 K: index 3,11, 1, 1
 K: index 3,11, 1, 2
 K: index 3,11, 1, 3
 K: index 3,11, 2, 1
 K: index 3,11, 2, 2
 K: index 3,11, 2, 3
 K: index 3,11, 3, 1
 K: index 3,11, 3, 2
 K: index 3,11, 3, 3
 K: index 3,12, 1, 1
 K: index 3,12, 1, 2
 K: index 3,12, 1, 3
 K: index 3,12, 2, 1
 K: index 3,12, 2, 2
 K: index 3,12, 2, 3
 K: index 3,12, 3, 1
 K: index 3,12, 3, 2
 K: index 3,12, 3, 3
 K: index 3,13, 1, 1
 K: index 3,13, 1, 2
 K: index 3,13, 1, 3
 K: index 3,13, 2, 1
 K: index 3,13, 2, 2
 K: index 3,13, 2, 3
 K: index 3,13, 3, 1
 K: in

In [10]:
# save("learned_filters_59_partial.jld","filters",h,"weights",weights_matrix)
# learned_filters = load("learned_filters_59_partial.jld","filters")

#With free 8 permutation matrices for existing patches
save("learned_filters_59_fullish.jld","filters",h,"weights",weights_matrix)
learned_filters = load("learned_filters_59_fullish.jld","filters")

24×3×3×4×25 Array{Float64,5}:
[:, :, 1, 1, 1] =
 1.71556e-5  1.56409e-5  1.59146e-5
 1.60232e-5  1.45188e-5  1.49262e-5
 1.99108e-5  1.62084e-5  1.59829e-5
 1.55394e-5  1.53322e-5  1.57777e-5
 1.54775e-5  1.49677e-5  1.56674e-5
 1.42661e-5  1.4806e-5   1.54572e-5
 2.26622e-5  1.9453e-5   1.7886e-5 
 1.73267e-5  1.80621e-5  1.75717e-5
 1.8299e-5   1.837e-5    1.74416e-5
 1.49376e-5  1.70617e-5  1.71696e-5
 1.69675e-5  2.01639e-5  1.9035e-5 
 1.67393e-5  1.72584e-5  1.68901e-5
 2.41556e-5  2.59907e-5  2.35526e-5
 1.86864e-5  1.84647e-5  1.79951e-5
 1.75089e-5  1.83363e-5  1.7613e-5 
 1.54685e-5  1.77528e-5  1.76459e-5
 2.16557e-5  2.36596e-5  1.77323e-5
 1.74007e-5  1.82377e-5  1.78668e-5
 1.54348e-5  1.53358e-5  1.548e-5  
 1.44869e-5  1.38307e-5  1.55869e-5
 1.85092e-5  1.56879e-5  1.56427e-5
 1.59188e-5  1.53941e-5  1.56608e-5
 1.53009e-5  1.50028e-5  1.52242e-5
 1.4563e-5   1.37524e-5  1.40725e-5

[:, :, 2, 1, 1] =
 2.00992e-5  1.64958e-5  1.72406e-5
 1.28037e-5  1.39998e-5  1.47164e